In [1]:
# пакет с предобученными свёрточными моделями  
# для расстановки ударений в тексте;
# %pip install git+https://github.com/Desklop/StressRNN

# пакет для транслитерации выражений на латинице;
# %pip install transliterate

Defaulting to user installation because normal site-packages is not writeable
  Cloning https://github.com/Desklop/StressRNN to /tmp/pip-req-build-4dnifsp5
  Running command git clone --filter=blob:none -q https://github.com/Desklop/StressRNN /tmp/pip-req-build-4dnifsp5
  Resolved https://github.com/Desklop/StressRNN to commit 6c8de89005be93a4a3cb2afbbe8e6d51405ffa6b
  Preparing metadata (setup.py) ... done
You should consider upgrading via the '/usr/local/bin/python3 -m pip install --upgrade pip' command.
Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/usr/local/bin/python3 -m pip install --upgrade pip' command.
Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/usr/local/bin/python3 -m pip install --upgrade pip' command.


In [25]:
# убрать warning'и;
from warnings import filterwarnings
filterwarnings('ignore')

In [26]:
import torch
# загрузить из репозитория модели silero в виде файла .yml;
torch.hub.download_url_to_file('https://raw.githubusercontent.com/snakers4/silero-models/master/models.yml',
                               'latest_silero_models.yml',
                               progress=False)

In [27]:
import os
import yaml
from torch import package

# из полученного файла достать tts-модели;
with open('latest_silero_models.yml', 'r') as yaml_file:
    models = yaml.load(yaml_file, Loader=yaml.SafeLoader)
tts_models = models['tts_models']['ru']

In [28]:
# посмотреть список доступных моделей;
tts_models

{'v3_1_ru': {'latest': {'example': 'В н+едрах т+ундры в+ыдры в г+етрах т+ырят в в+ёдра +ядра к+едров.',
   'package': 'https://models.silero.ai/models/tts/ru/v3_1_ru.pt',
   'sample_rate': [8000, 24000, 48000]}},
 'ru_v3': {'latest': {'example': 'В н+едрах т+ундры в+ыдры в г+етрах т+ырят в в+ёдра +ядра к+едров.',
   'package': 'https://models.silero.ai/models/tts/ru/ru_v3.pt',
   'sample_rate': [8000, 24000, 48000]}},
 'aidar_v2': {'latest': {'example': 'В н+едрах т+ундры в+ыдры в г+етрах т+ырят в в+ёдра +ядра к+едров.',
   'package': 'https://models.silero.ai/models/tts/ru/v2_aidar.pt',
   'sample_rate': [8000, 16000]}},
 'aidar_8khz': {'latest': {'tokenset': '_~абвгдеёжзийклмнопрстуфхцчшщъыьэюя +.,!?…:;–',
   'example': 'В н+едрах т+ундры в+ыдры в г+етрах т+ырят в в+ёдра +ядра к+едров.',
   'jit': 'https://models.silero.ai/models/tts/ru/v1_aidar_8000.jit',
   'sample_rate': 8000},
  'v1': {'tokenset': '_~абвгдеёжзийклмнопрстуфхцчшщъыьэюя +.,!?…:;–',
   'example': 'В н+едрах т+ундры в

In [29]:
tts_models_v3_ru = tts_models['v3_1_ru']
tts_models_v3_ru

{'latest': {'example': 'В н+едрах т+ундры в+ыдры в г+етрах т+ырят в в+ёдра +ядра к+едров.',
  'package': 'https://models.silero.ai/models/tts/ru/v3_1_ru.pt',
  'sample_rate': [8000, 24000, 48000]}}

In [30]:
# получить ссылку на необходимую модель;
model_url = tts_models_v3_ru['latest']['package']

# создать директорию для хранения файла загруженной модели;
model_dir = "downloaded_model"
os.makedirs(model_dir, exist_ok=True)
model_path = os.path.join(model_dir, os.path.basename(model_url))

# загрузить модель;
if not os.path.isfile(model_path):
    torch.hub.download_url_to_file(model_url,
                                   model_path,
                                   progress=True)
# импортировать модель из файла    
imp = package.PackageImporter(model_path)
model = imp.load_pickle("tts_models", "model")

In [32]:
# пример обработки короткой строки, не длиннее 140 символов
from IPython.display import Audio, display

# настройки модели
speaker = 'xenia' # 'aidar', 'baya', 'kseniya', 'xenia', 'eugene', 'random';
# частота звуковой волны
sample_rate = 48000 # 8000, 24000, 48000;
# доступен выбор между cpu и gpu;

# device = torch.device('cpu')
# model.to(device)

example_text = input()
if len(example_text) > 520:
    print("Слишком большая строка!")
else:
    # на выходе модели получается тензор вещественных чисел;
    audio = model.apply_tts(text=example_text,
                            speaker=speaker,
                            sample_rate=sample_rate,
                            put_accent=True, # расстановка ударений самой моделью;
                            put_yo=True # расставлять `ё` там, где её нет;
                           )
    display(Audio(audio, rate=sample_rate))

# Мандельштама читает непллохо.

 Возьми на радость из моих ладоней Немного солнца и немного мёда, Как нам велели пчёлы Персефоны.  Не отвязать неприкреплённой лодки, Не услыхать в меха обутой тени, Не превозмочь в дремучей жизни страха.  Нам остаются только поцелуи, Мохнатые, как маленькие пчёлы, Что умирают, вылетев из улья.  Они шуршат в прозрачных дебрях ночи, Их родина — дремучий лес Тайг+ета, Их пища — время, медуница, мята.  Возьми ж на радость дикий мой подарок, — Невзрачное сухое ожерелье, Из мертвых пчёл, мёд превративших в солнце.


In [8]:
ssml_sample = """
              <speak>
              <p>
                  Когда я просыпаюсь, <prosody rate="x-slow">я говорю довольно медленно</prosody>.
                  Пот+ом я начинаю говорить своим обычным голосом,
                  <prosody pitch="x-high"> а могу говорить тоном выше </prosody>,
                  или <prosody pitch="x-low">наоборот, ниже</prosody>.
                  Пот+ом, если повезет – <prosody rate="fast">я могу говорить и довольно быстро.</prosody>
                  А еще я умею делать паузы любой длины, например, две секунды <break time="2000ms"/>.
                  <p>
                    Также я умею делать паузы между параграфами.
                  </p>
                  <p>
                    <s>И также я умею делать паузы между предложениями</s>
                    <s>Вот например как сейчас</s>
                  </p>
              </p>
              </speak>
              """
audio = model.apply_tts(text=ssml_sample,
                        speaker=speaker,
                        sample_rate=sample_rate)
Audio(audio, rate=sample_rate)

# не было замечено, чтобы разметка как-то влияла на произносимую речь,
# паузы выдерживаются, но в первом предложении замедления речи не было;

In [9]:
from stressrnn import StressRNN

In [10]:
import re
import wave
import numpy
import numtext

from transliterate import translit
from scipy.io.wavfile import write


def transl(text):
    """
    Функция транслитерирует слова, написанные латиницей.
    """
    text=text.lower()
    s_rus=translit(text, 'ru')
    s_rus=s_rus.replace('w','в')
    return(s_rus)


def delstress(text):
    """ 
    Функция удаляет неправильно расставленные ударения. 
    """
    text = text.lower()
    m = ['б','й','в','г','д','ж','з','к','л','м','н','п','р','с','т','ф','х','ц','ч','ш','щ','ъ','ь']
    for xx in m:
        text = text.replace('+'+xx, xx)
    mas = text.strip().split(' ')
    if(mas[-1].count('+') > 1 and text[-2]=='+'):
        text = text[:-2]+text[-1]
        
    gl = ['а','у','е','ы','а','о','э','я','и','ю','ё']
    mas = text.strip().split(' ')
    text2 = ''
    for z in mas:
        flag = 0
        for r in z:
            if r in gl:
                flag += 1   
        if(flag==1 and not '+' in z):
            for r in gl:
                z = z.replace(r,'+'+r)
        if len(re.findall(r'\+', z)) > 1:
            z = z.replace('+'+z[z.find('+')], z[z.find('+')])
        text2=text2+z+' '
    return text2

def getpr(t):
    """
    Функция делит текст на массив предложений.
    """
    t=t.strip()
    t=t.replace('\n','.')
    t=t.replace('\t','.')
    t=t.replace('\r','.')
    t=t.replace(';','.')
    t=t.replace(':', '.')
    t=t.replace('…','.')
    t=t.replace('..',' ')
    t=t.replace('...',' ')
    mas=re.split("\\b[.!?\\n]+(?=\\s)", t)
    return mas


def float_to_int(wav):
    """ 
    Функция конвертирует float в int.
    """
    wav *= 32767
    wav = wav.astype('int16')
    return wav

def sayit(text, filename):
    """
    Функция 
    """
    stressed_text = stress_rnn.put_stress(text, 
                                          stress_symbol='+', 
                                          accuracy_threshold=0.90, 
                                          replace_similar_symbols=True
                                         )
    stressed_text = stressed_text.split('+')
    stressed_text_marked = ''
    for lex in stressed_text:
        try:
            if(lex != ''):
                s = lex[:-1] + '+' + lex[-1]
            else:
                s = lex
            stressed_text_marked += s
        except:
            pass
    stressed_text_marked = delstress(stressed_text_marked)
    os.makedirs('static', exist_ok=True)
    createwav(stressed_text_marked, f"static/{filename}.wav")
    
    
def createwav(text, wavname):
    """
    Функция создаёт .wav файл.
    Аргументы:
        text - размеченная строка текста;
        wavname - имя файла, строка.
    """
    # разбить на массив предложений полученный текст;
    texts = getpr(text)
    # список для хранения выходных тензоров модели;
    data = []
    for text in texts:
        print(f"{text}\n")
        if text.strip() != '.' or text != '':
            # тензор для каждого полученного отрезка;
            audio = model.apply_tts(text=text,
                                    speaker=speaker,
                                    sample_rate=sample_rate,
                                    put_accent=True,
                                    put_yo=True
                                   )
            # добавление целочисленного тензора в колллекцию;
            data.append(float_to_int(audio.numpy()))
    # склейка всех полученных массивов в один большой;
    data = numpy.concatenate(data, axis=0)
    # конвертация полученного вектора в аудиофайл;
    write(wavname, rate=sample_rate, data=data)


def say_big_text(text, filename):
    """
    Функция для синтеза больших текстов.
    Аргументы:
        text - исходный текст файла;
        filename - имя файла с текстом.
    """
    text = numtext.getnumbers(text)
    text = transl(text)
    sayit(text, filename)

In [11]:
def say_book(filename):
    f = open(filename, 'r', encoding='UTF-8')
    x = f.read()
    f.close()
    filename = filename.split('.')[0].split('/')[-1]
    say_big_text(x, filename)

In [12]:
stress_rnn= StressRNN()
say_book(f'5.txt')
Audio('static/5.wav', rate=sample_rate)

реш+ение +этого вопр+оса оп+исано в инстр+укции н+а корпорат+ивном порт+але, в разд+еле б+аза зн+аний

 в п+оиске напиш+ите назв+ание инстр+укции

 +у в+ас +это пол+учится быстр+ее, ч+ем пок+а специал+исты в пор+ядке +очереди, найд+ут н+ужную.



In [15]:
21*9

189